## Prog 5: Nifty PCR calculation (Nitin Murakka)

## 6 Aug 24 : Program version 2 : 2030 Hrs 

In [1]:
import pandas as pd
from openpyxl import Workbook, load_workbook
from openpyxl.styles import PatternFill, Alignment
from openpyxl.chart import LineChart, Reference
from openpyxl.utils.dataframe import dataframe_to_rows
from datetime import datetime
import requests
import os
import time
import threading
import math
import signal
import sys

# Initialize session object
session = requests.Session()
headers = {
    'user-agent': "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/17.4.1 Safari/605.1.15",
}

stop_thread = threading.Event()

def get_cookie():
    url = 'https://www.nseindia.com'
    response = session.get(url, headers=headers)
    cookies = response.cookies.get_dict()
    cookie_str = '; '.join([f"{key}={value}" for key, value in cookies.items()])
    return cookie_str

def fetch_data(url):
    retries = 3
    for attempt in range(retries):
        headers['cookie'] = get_cookie()
        try:
            response = session.get(url, headers=headers)
            response.raise_for_status()
            return response.json()
        except requests.exceptions.HTTPError as e:
            if response.status_code in [401, 403]:
                print(f"Attempt {attempt + 1}: Cookie expired. Fetching a new cookie...")
            else:
                print(f"HTTP Error {response.status_code}: {response.text}")
                break
        except requests.exceptions.RequestException as e:
            print(f"Request Error: {e}")
            break
    return None

def get_user_input(expiry_dates):
    try:
        underlying_price = float(input("Enter the underlying price of Nifty: "))
    except ValueError:
        print("Invalid input. Please enter a number.")
        return None, None, None, None

    nearest_multiple_of_50 = math.floor(underlying_price / 50) * 50

    print("\nChoose the Lower Strike option from the following:")
    lower_strike_options = [nearest_multiple_of_50 - i * 50 for i in range(0, 5)]
    for i, strike_price in enumerate(lower_strike_options, start=1):
        print(f"{i}: {strike_price}")

    try:
        lower_strike_option = int(input("Enter the option number for Lower_strike_price: "))
        lower_strike = lower_strike_options[lower_strike_option - 1]
    except (ValueError, IndexError):
        print("Invalid input for Lower_strike_price.")
        return None, None, None, None

    print("\nChoose the Upper Strike option from the following:")
    upper_strike_options = [nearest_multiple_of_50 + (i + 1) * 50 for i in range(0, 5)]
    for i, strike_price in enumerate(upper_strike_options, start=1):
        print(f"{i}: {strike_price}")

    try:
        upper_strike_option = int(input("Enter the option number for Upper_Strike_Price: "))
        upper_strike = upper_strike_options[upper_strike_option - 1]
    except (ValueError, IndexError):
        print("Invalid input for Upper_Strike_Price.")
        return None, None, None, None

    print("\nChoose the Expiry Date option from the following:")
    for i, expiry_date in enumerate(expiry_dates, start=1):
        print(f"{i}: {expiry_date}")

    try:
        expiry_date_option = int(input("Enter the option number for Expiry Date: "))
        selected_expiry_date = expiry_dates[expiry_date_option - 1]
    except (ValueError, IndexError):
        print("Invalid input for Expiry Date.")
        return None, None, None, None

    return underlying_price, lower_strike, upper_strike, selected_expiry_date

def get_expiry_dates():
    url = 'https://www.nseindia.com/api/liveEquity-derivatives?index=nse50_opt'
    data = fetch_data(url)
    if data is None or 'data' not in data:
        print("Failed to fetch data.")
        return []

    records = data['data']
    
    # Filter records to include only those relevant to NIFTY
    nifty_records = [entry for entry in records if entry['underlying'] == 'NIFTY']
    
    # Extract unique expiry dates from the filtered records
    expiry_dates = list(set([entry['expiryDate'] for entry in nifty_records]))
    
    # Convert date strings to datetime objects for sorting
    expiry_dates = sorted(expiry_dates, key=lambda date: datetime.strptime(date, '%d-%b-%Y'))
    
    # Limit the result to the first five dates
    expiry_dates = expiry_dates[:5]
    
    return expiry_dates

def generate_option_chain(url, expiry_date):
    data = fetch_data(url)
    if data is None or 'data' not in data:
        print(f"Failed to fetch data from {url}")
        return []

    records = data['data']
    filtered_data = [entry for entry in records if entry['expiryDate'] == expiry_date]
    return filtered_data

def preprocess_option_data(option_chain_data, lower_strike, upper_strike):
    cleaned_data = []
    strike_data = {}

    for entry in option_chain_data:
        if 'identifier' not in entry or entry['strikePrice'] < lower_strike or entry['strikePrice'] > upper_strike:
            continue  # Skip if identifier is not available or strike price is out of range
        strike_price = entry.get('strikePrice', 0)
        expiry_date = entry.get('expiryDate', '')

        if strike_price not in strike_data:
            strike_data[strike_price] = {
                'Strike Price': strike_price,
                'Expiry Date': expiry_date,
                'Put Last Price': 0,
                'T_Put_OI': 0,
                'Put Change in OI': 0,
                'Call Last Price': 0,
                'T_Call_OI': 0,
                'Call Change in OI': 0
            }

        if 'PE' in entry['identifier']:
            strike_data[strike_price].update({
                'Put Last Price': float(entry.get('lastPrice', 0)),
                'T_Put_OI': int(entry.get('openInterest', 0)),
                'Put Change in OI': int(entry.get('changeinOpenInterest', 0))
            })

        elif 'CE' in entry['identifier']:
            strike_data[strike_price].update({
                'Call Last Price': float(entry.get('lastPrice', 0)),
                'T_Call_OI': int(entry.get('openInterest', 0)),
                'Call Change in OI': int(entry.get('changeinOpenInterest', 0))
            })

    for strike, data in strike_data.items():
        cleaned_data.append(data)

    return cleaned_data

def create_excel_with_layout(data, file_path, underlying_price):
    wb = Workbook()
    ws2 = wb.active
    ws2.title = 'Nifty_Range_PCR'  # Renamed sheet

    headers = [
        ("Month", "Aug", "", "Week", "1W", "Underlying", underlying_price, "IMBALANCE"),
        ("Underlying", "Strike", "LTP_Put", "put_OI", "Strike", "LTP_Call", "Call_OI", "Call COI", "Put COI", "DIFF", "PCR")
    ]

    for row_num, header in enumerate(headers, 1):
        for col_num, header_text in enumerate(header, 1):
            cell = ws2.cell(row=row_num, column=col_num, value=header_text)
            cell.alignment = Alignment(horizontal='center', vertical='center')
            if row_num == 1:
                cell.fill = PatternFill(start_color='FFFF00', end_color='FFFF00', fill_type='solid')

    closest_strike_price = min(data, key=lambda x: abs(x['Strike Price'] - underlying_price))['Strike Price']

    for row in sorted(data, key=lambda x: x['Strike Price']):
        strike_price = row['Strike Price']
        put_last_price = row['Put Last Price']
        t_put_oi = row['T_Put_OI']
        call_last_price = row['Call Last Price']
        t_call_oi = row['T_Call_OI']
        
        if t_call_oi and t_put_oi:
            call_coi = (int(t_call_oi) / (int(t_call_oi) + int(t_put_oi))) * 100
            put_coi = (int(t_put_oi) / (int(t_call_oi) + int(t_put_oi))) * 100
            diff = put_coi - call_coi
        else:
            call_coi = ""
            put_coi = ""
            diff = ""

        pcr = int(t_put_oi) / int(t_call_oi) if t_call_oi else ""

        # Insert underlying price only in the row closest to the strike price
        if strike_price == closest_strike_price:
            ws2.append([underlying_price, strike_price, put_last_price, t_put_oi, strike_price, call_last_price, t_call_oi, call_coi, put_coi, diff, pcr])
        else:
            ws2.append(["", strike_price, put_last_price, t_put_oi, strike_price, call_last_price, t_call_oi, call_coi, put_coi, diff, pcr])

    # Capture values before adding the SUM formulas
    sum_put_oi = sum([row[3].value for row in ws2.iter_rows(min_row=3, max_row=ws2.max_row)])
    sum_call_oi = sum([row[6].value for row in ws2.iter_rows(min_row=3, max_row=ws2.max_row)])
    sum_call_coi = sum([row[7].value for row in ws2.iter_rows(min_row=3, max_row=ws2.max_row)])
    sum_put_coi = sum([row[8].value for row in ws2.iter_rows(min_row=3, max_row=ws2.max_row)])
    sum_diff = sum([row[9].value for row in ws2.iter_rows(min_row=3, max_row=ws2.max_row)])
    pcr_value = sum_put_coi / sum_call_coi if sum_call_coi != 0 else 0

    # Adding SUM formula for Call_OI, put_OI, Call COI, Put COI, and DIFF in Nifty_Range_PCR
    max_row = ws2.max_row
    ws2.cell(row=max_row + 1, column=4, value=f"=SUM(D3:D{max_row})")
    ws2.cell(row=max_row + 1, column=7, value=f"=SUM(G3:G{max_row})")
    ws2.cell(row=max_row + 1, column=8, value=f"=SUM(H3:H{max_row})")
    ws2.cell(row=max_row + 1, column=9, value=f"=SUM(I3:I{max_row})")
    ws2.cell(row=max_row + 1, column=10, value=f"=SUM(J3:J{max_row})")

    # Adding PCR calculation below the sum rows
    ws2.cell(row=max_row + 1, column=11, value=f"=I{max_row + 1}/H{max_row + 1}")

    # Pre-calculate DIFF sum for styling
    diff_sum = sum([row[9].value for row in ws2.iter_rows(min_row=3, max_row=max_row) if row[9].value is not None])

    # Apply styles to the final DIFF cell
    diff_final_cell = ws2.cell(row=max_row + 1, column=10)
    # diff_final_cell = ws2.cell(row=max_row + 1, column=10)
    try:
        if diff_sum < 0:
            diff_final_cell.fill = PatternFill(start_color='FF0000', end_color='FF0000', fill_type='solid')
        else:
            diff_final_cell.fill = PatternFill(start_color='00FF00', end_color='00FF00', fill_type='solid')
    except ValueError:
        print(f"Error converting DIFF value: {diff_final_cell.value}")

    apply_styles_with_layout(ws2)

    # Save the workbook and also store the calculated values
    wb.save(file_path)
    # print(f"Data saved to {file_path} at {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")

    # Return captured values for Last_Row_Data
    return {
        "sum_put_oi": sum_put_oi,
        "sum_call_oi": sum_call_oi,
        "sum_call_coi": sum_call_coi,
        "sum_put_coi": sum_put_coi,
        "sum_diff": sum_diff,
        "pcr_value": pcr_value
    }

def apply_styles_with_layout(ws):
    red_fill = PatternFill(start_color='FF0000', end_color='FF0000', fill_type='solid')
    green_fill = PatternFill(start_color='00FF00', end_color='00FF00', fill_type='solid')
    orange_fill = PatternFill(start_color='FFA500', end_color='FFA500', fill_type='solid')

    # Highlight the largest value in Call COI and Put COI columns
    max_call_coi = 0
    max_put_coi = 0
    max_call_coi_cell = None
    max_put_coi_cell = None

    for row in ws.iter_rows(min_row=3, max_row=ws.max_row-1, min_col=8, max_col=9):  # Columns H and I
        call_coi = row[0].value
        put_coi = row[1].value
        if call_coi is not None and call_coi > max_call_coi:
            max_call_coi = call_coi
            max_call_coi_cell = row[0]
        if put_coi is not None and put_coi > max_put_coi:
            max_put_coi = put_coi
            max_put_coi_cell = row[1]

    if max_call_coi_cell:
        max_call_coi_cell.fill = orange_fill
    if max_put_coi_cell:
        max_put_coi_cell.fill = orange_fill

    for row in ws.iter_rows(min_row=3, max_col=ws.max_column):
        row[2].fill = red_fill
        row[5].fill = green_fill

    ws.freeze_panes = 'A3'

def save_to_csv(data, filename):
    df = pd.DataFrame(data)
    if not os.path.isfile(filename):
        df.to_csv(filename, mode='w', header=True, index=False)
    else:
        df.to_csv(filename, mode='a', header=False, index=False)

def save_pcr_to_csv(pcr, filename):
    timestamp = datetime.now().strftime('%Y-%m-%d %H:%M:%S')
    new_data = pd.DataFrame({'Timestamp': [timestamp], 'PCR': [pcr]})
    if not os.path.isfile(filename):
        new_data.to_csv(filename, mode='w', header=True, index=False)
    else:
        new_data.to_csv(filename, mode='a', header=False, index=False)

def csv_to_excel(csv_filename, excel_filename, sheet_name):
    df = pd.read_csv(csv_filename)
    with pd.ExcelWriter(excel_filename, engine='openpyxl') as writer:
        df.to_excel(writer, sheet_name=sheet_name, index=False)
    # print(f"CSV data from {csv_filename} saved to Excel file {excel_filename}")

def merge_csv_files_to_excel(csv_files, excel_filename, sheet_names):
    with pd.ExcelWriter(excel_filename, engine='openpyxl') as writer:
        for csv_file, sheet_name in zip(csv_files, sheet_names):
            df = pd.read_csv(csv_file)
            df.to_excel(writer, sheet_name=sheet_name, index=False)
            # print(f"Data from {csv_file} saved to {excel_filename} in sheet {sheet_name}")

def fetch_and_save_to_csv():
    url = 'https://www.nseindia.com/api/liveEquity-derivatives?index=nse50_opt'
    csv_filename = 'Nifty_PCR.csv'
    timeseries_csv_filename = 'Nifty_PCR_Timeseries.csv'
    global stop_thread
    while not stop_thread.is_set():
        data = fetch_data(url)
        if data:
            records = data.get('data', [])
            df_data = []
            for rec in records:
                try:
                    df_data.append({
                        'symbol': rec['identifier'],
                        'lastPrice': rec['lastPrice'],
                        'openInterest': rec['openInterest'],
                        'changeinOpenInterest': rec.get('changeinOpenInterest', None)
                    })
                except KeyError as e:
                    print(f"Missing key {e} in record: {rec}")
            save_to_csv(df_data, csv_filename)
            time_now = datetime.now().strftime('%H:%M:%S')
            # print(f"Data saved to {csv_filename} and {timeseries_csv_filename} at : {time_now}")
            
            # Generate time series data
            time_series_data = generate_time_series_data(df_data)
            save_to_csv(time_series_data, timeseries_csv_filename)
            # print(f"Time series data saved to {timeseries_csv_filename} at : {time_now}")
        time.sleep(60)

def generate_time_series_data(df_data):
    time_series_data = []
    timestamp = datetime.now().strftime('%H:%M')
    call_oi = sum([int(item['openInterest']) for item in df_data if 'CE' in item['symbol']])
    put_oi = sum([int(item['openInterest']) for item in df_data if 'PE' in item['symbol']])
    diff = put_oi - call_oi
    pcr = put_oi / call_oi if call_oi > 0 else 0
    option_signal = 'BUY' if pcr > 1 else 'SELL'
    vwap = calculate_vwap(df_data)
    price = calculate_price(df_data)
    vwap_signal = 'BUY' if price > vwap else 'SELL'

    time_series_data.append({
        'Time': timestamp,
        'Call': call_oi,
        'Put': put_oi,
        'Diff': diff,
        'PCR': pcr,
        'Option Signal': option_signal,
        'VWAP': vwap,
        'Price': price,
        'VWAP Signal': vwap_signal
    })

    return time_series_data

def calculate_vwap(df_data):
    # Placeholder function to calculate VWAP from df_data
    return 0

def calculate_price(df_data):
    # Placeholder function to calculate Price from df_data
    return 0

def update_excel_with_timeseries(excel_filename, timeseries_csv_filename):
    wb = load_workbook(excel_filename)
    if 'TimeSeries' not in wb.sheetnames:
        ws = wb.create_sheet(title='TimeSeries')
        headers = ['Time', 'Call', 'Put', 'Diff', 'PCR', 'Option Signal', 'VWAP', 'Price', 'VWAP Signal']
        ws.append(headers)
    else:
        ws = wb['TimeSeries']

    df = pd.read_csv(timeseries_csv_filename)
    for index, row in df.iterrows():
        ws.append(row.tolist())

    wb.save(excel_filename)
    print(f"Data and Time series data saved to {excel_filename} at : {datetime.now().strftime('%H:%M:%S')}")

def generate_line_chart(excel_filename):
    wb = load_workbook(excel_filename)
    if 'Sheet4' not in wb.sheetnames:
        ws4 = wb.create_sheet(title='Sheet4')
    else:
        ws4 = wb['Sheet4']

    df = pd.read_csv('Nifty_PCR_Timeseries.csv')
    for r in dataframe_to_rows(df, index=False, header=True):
        ws4.append(r)

    max_row = ws4.max_row
    max_col = ws4.max_column

    chart = LineChart()
    chart.title = "PCR Time Series"
    chart.style = 13
    chart.y_axis.title = 'PCR'
    chart.x_axis.title = 'Time'

    data = Reference(ws4, min_col=5, min_row=1, max_col=5, max_row=max_row)  # PCR data is in the 5th column
    categories = Reference(ws4, min_col=1, min_row=2, max_row=max_row)  # Time data is in the 1st column
    chart.add_data(data, titles_from_data=True)
    chart.set_categories(categories)

    ws4.add_chart(chart, "A10")
    wb.save(excel_filename)
    # print(f"Line chart generated in Sheet4 of {excel_filename} at {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")

def extract_and_append_last_row_data_to_csv(calculated_values, csv_filename):
    timestamp = datetime.now().strftime('%Y-%m-%d %H:%M:%S')
    last_row_data = [timestamp, "", calculated_values['sum_put_oi'], calculated_values['sum_call_oi'],
                     calculated_values['sum_call_coi'], calculated_values['sum_put_coi'], calculated_values['sum_diff'],
                     calculated_values['pcr_value']]

    # Append the data to the CSV file
    df = pd.DataFrame([last_row_data], columns=['Timestamp', 'Underlying', 'put_OI', 'Call_OI', 'Call COI', 'Put COI', 'DIFF', 'PCR'])
    if not os.path.isfile(csv_filename):
        df.to_csv(csv_filename, mode='w', header=True, index=False)
    else:
        df.to_csv(csv_filename, mode='a', header=False, index=False)
    # print(f"Last row data appended to CSV file {csv_filename} at {timestamp}")

def update_excel_from_csv(csv_filename, excel_filename, sheet_name):
    # Read the CSV file
    df = pd.read_csv(csv_filename)

    # Load the existing workbook or create a new one
    if os.path.exists(excel_filename):
        wb = load_workbook(excel_filename)
    else:
        wb = Workbook()

    if sheet_name not in wb.sheetnames:
        ws = wb.create_sheet(title=sheet_name)
        headers = ['Timestamp', 'Underlying', 'put_OI', 'Call_OI', 'Call COI', 'Put COI', 'DIFF', 'PCR']
        ws.append(headers)
    else:
        ws = wb[sheet_name]

    # Append rows from the DataFrame to the Excel sheet
    for row in dataframe_to_rows(df, index=False, header=False):
        ws.append(row)

    # Apply styles to the 'DIFF' column
    for row in ws.iter_rows(min_row=2, max_row=ws.max_row, min_col=7, max_col=7):
        for cell in row:
            try:
                diff_value = float(cell.value)
                if diff_value < 0:
                    cell.fill = PatternFill(start_color='FF0000', end_color='FF0000', fill_type='solid')  # Red fill for negative values
                else:
                    cell.fill = PatternFill(start_color='00FF00', end_color='00FF00', fill_type='solid')  # Green fill for positive values
            except (ValueError, TypeError):
                pass  # Skip cells that cannot be converted to float

    wb.save(excel_filename)
    # print(f"CSV data from {csv_filename} appended to '{sheet_name}' sheet in {excel_filename}")

def signal_handler(sig, frame):
    global stop_thread
    stop_thread.set()
    print('Stopping the data fetching thread...')
    sys.exit(0)

def main():
    signal.signal(signal.SIGINT, signal_handler)  # Handle Ctrl+C
    expiry_dates = get_expiry_dates()
    if not expiry_dates:
        print("No expiry dates available.")
        return

    underlying_price, lower_strike, upper_strike, expiry_date = get_user_input(expiry_dates)
    if underlying_price is None:
        return

    global csv_thread
    csv_thread = threading.Thread(target=fetch_and_save_to_csv)
    csv_thread.start()

    while not stop_thread.is_set():
        csv_filename = 'Nifty_PCR.csv'
        excel_filename = 'Nifty_PCR.xlsx'
        timeseries_csv_filename = 'Nifty_PCR_Timeseries.csv'
        last_row_csv_filename = 'Nifty_Last_Row_Data.csv'
        last_row_data_sheet_name = 'Last_Row_Data'

        if os.path.isfile(csv_filename):
            csv_to_excel(csv_filename, excel_filename, 'Sheet2')
            option_chain_data = generate_option_chain('https://www.nseindia.com/api/liveEquity-derivatives?index=nse50_opt', expiry_date)
            if option_chain_data:
                preprocessed_data = preprocess_option_data(option_chain_data, lower_strike, upper_strike)
                calculated_values = create_excel_with_layout(preprocessed_data, excel_filename, underlying_price)
                update_excel_with_timeseries(excel_filename, timeseries_csv_filename)
                generate_line_chart(excel_filename)
                # Extract and append the last row data to CSV
                extract_and_append_last_row_data_to_csv(calculated_values, last_row_csv_filename)
                # Update Excel from the CSV file
                update_excel_from_csv(last_row_csv_filename, excel_filename, last_row_data_sheet_name)
        time.sleep(60)

if __name__ == "__main__":
    main()


Choose the Lower Strike option from the following:
1: 24300
2: 24250
3: 24200
4: 24150
5: 24100

Choose the Upper Strike option from the following:
1: 24350
2: 24400
3: 24450
4: 24500
5: 24550

Choose the Expiry Date option from the following:
1: 14-Aug-2024
2: 22-Aug-2024
3: 29-Aug-2024
4: 05-Sep-2024
5: 12-Sep-2024
Attempt 1: Cookie expired. Fetching a new cookie...
Attempt 1: Cookie expired. Fetching a new cookie...
Data and Time series data saved to Nifty_PCR.xlsx at : 15:50:17
Attempt 1: Cookie expired. Fetching a new cookie...
Data and Time series data saved to Nifty_PCR.xlsx at : 15:51:20
Attempt 1: Cookie expired. Fetching a new cookie...
Data and Time series data saved to Nifty_PCR.xlsx at : 15:52:24
Attempt 1: Cookie expired. Fetching a new cookie...
Data and Time series data saved to Nifty_PCR.xlsx at : 15:53:25
Attempt 1: Cookie expired. Fetching a new cookie...
Data and Time series data saved to Nifty_PCR.xlsx at : 15:54:27
Attempt 1: Cookie expired. Fetching a new cookie

## LIVE PCR Chart 

In [11]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load the CSV file
csv_file_path = "/Users/tjzoomac/tj_nse/ai_market/01_nifty_live/002/Nifty_PCR_Timeseries.csv"
df = pd.read_csv(csv_file_path)

# Convert the 'Time' column to datetime, ensure it's correctly parsed
df['Time'] = pd.to_datetime(df['Time'], format='%H:%M')

# Rename columns for clarity
df.rename(columns={'Time': 'timestamp', 'PCR': 'pcr'}, inplace=True)

# Debugging: Check the data
print(df[['timestamp', 'pcr']].head())

# Create a figure
fig = make_subplots(rows=1, cols=1)

# Add a trace for the line plot
fig.add_trace(go.Scatter(x=df['timestamp'], y=df['pcr'], mode='lines', name='PCR over time'))

# Set up the layout
fig.update_layout(title='PCR over Time',
                  xaxis_title='Time',
                  yaxis_title='PCR Value',
                  xaxis=dict(tickformat='%H:%M'))

# Update frames for animation
frames = [go.Frame(data=[go.Scatter(x=df['timestamp'][:k+1], y=df['pcr'][:k+1])], name=f'frame{k}') for k in range(len(df))]

fig.update(frames=frames)

# Set up animation settings
fig.update_layout(updatemenus=[dict(type='buttons', showactive=False,
                                    buttons=[dict(label='Play', method='animate',
                                                  args=[None, dict(frame=dict(duration=100, redraw=True), fromcurrent=True)])])])

# Show the plot
fig.show()


            timestamp       pcr
0 1900-01-01 09:26:00  0.764393
1 1900-01-01 09:27:00  0.784947
2 1900-01-01 09:28:00  0.784888
3 1900-01-01 09:29:00  0.785031
4 1900-01-01 09:30:00  0.785031


## Multiple Chart Visibility and analysis

In [6]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load the CSV files
pcr_csv_file_path = "/Users/tjzoomac/tj_nse/ai_market/01_nifty_live/002/Nifty_PCR_Timeseries.csv"
last_row_csv_file_path = "/Users/tjzoomac/tj_nse/ai_market/01_nifty_live/002/Nifty_Last_Row_Data.csv"

# Load the dataframes
pcr_df = pd.read_csv(pcr_csv_file_path)
last_row_df = pd.read_csv(last_row_csv_file_path)

# Convert the 'Time' column to datetime, ensure it's correctly parsed
pcr_df['Time'] = pd.to_datetime(pcr_df['Time'], format='%H:%M')
last_row_df['Timestamp'] = pd.to_datetime(last_row_df['Timestamp'], format='%Y-%m-%d %H:%M:%S')

# Rename columns for clarity
pcr_df.rename(columns={'Time': 'timestamp', 'PCR': 'pcr'}, inplace=True)
last_row_df.rename(columns={'Timestamp': 'timestamp', 'put_OI': 'put_oi', 'Call_OI': 'call_oi'}, inplace=True)

# Debugging: Check the data
print(pcr_df[['timestamp', 'pcr']].head())
print(last_row_df[['timestamp', 'put_oi', 'call_oi']].head())

# Create a figure with 3 subplots
fig = make_subplots(rows=3, cols=1, shared_xaxes=True,
                    subplot_titles=('PCR over Time', 'put_OI over Time', 'call_OI over Time'))

# Add a trace for the PCR line plot
fig.add_trace(go.Scatter(x=pcr_df['timestamp'], y=pcr_df['pcr'], mode='lines', name='PCR over time'), row=1, col=1)

# Add a trace for the put_OI line plot
fig.add_trace(go.Scatter(x=last_row_df['timestamp'], y=last_row_df['put_oi'], mode='lines', name='put_OI over time'), row=2, col=1)

# Add a trace for the call_OI line plot
fig.add_trace(go.Scatter(x=last_row_df['timestamp'], y=last_row_df['call_oi'], mode='lines', name='call_OI over time'), row=3, col=1)

# Set up the layout
fig.update_layout(title='Nifty PCR and OI over Time',
                  xaxis=dict(tickformat='%H:%M'),
                  xaxis2=dict(tickformat='%H:%M'),
                  xaxis3=dict(tickformat='%H:%M'),
                  yaxis_title='PCR Value',
                  yaxis2_title='put_OI Value',
                  yaxis3_title='call_OI Value')

# Update frames for animation for each subplot
pcr_frames = [go.Frame(data=[go.Scatter(x=pcr_df['timestamp'][:k+1], y=pcr_df['pcr'][:k+1])], name=f'pcr_frame{k}') for k in range(len(pcr_df))]
put_oi_frames = [go.Frame(data=[go.Scatter(x=last_row_df['timestamp'][:k+1], y=last_row_df['put_oi'][:k+1])], name=f'put_oi_frame{k}') for k in range(len(last_row_df))]
call_oi_frames = [go.Frame(data=[go.Scatter(x=last_row_df['timestamp'][:k+1], y=last_row_df['call_oi'][:k+1])], name=f'call_oi_frame{k}') for k in range(len(last_row_df))]

fig.update(frames=pcr_frames + put_oi_frames + call_oi_frames)

# Set up animation settings
fig.update_layout(updatemenus=[dict(type='buttons', showactive=False,
                                    buttons=[dict(label='Play', method='animate',
                                                  args=[None, dict(frame=dict(duration=100, redraw=True), fromcurrent=True)])])])

# Show the plot
fig.show()


            timestamp       pcr
0 1900-01-01 09:26:00  0.764393
1 1900-01-01 09:27:00  0.784947
2 1900-01-01 09:28:00  0.784888
3 1900-01-01 09:29:00  0.785031
4 1900-01-01 09:30:00  0.785031
            timestamp  put_oi  call_oi
0 2024-08-07 09:27:09  357110   496116
1 2024-08-07 09:28:10  357110   496116
2 2024-08-07 09:29:11  357110   496116
3 2024-08-07 09:30:15  357110   496248
4 2024-08-07 09:31:16  393418   508201


In [7]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load the Excel file
excel_file_path = "/Users/tjzoomac/tj_nse/ai_market/01_nifty_live/002/Nifty_PCR_Timeseries.csv"
df = pd.read_excel(excel_file_path, sheet_name='TimeSeries')

# Convert the 'Time' column to datetime, ensure it's correctly parsed
df['Time'] = pd.to_datetime(df['Time'], format='%H:%M')

# Rename columns for clarity
df.rename(columns={'Time': 'timestamp', 'PCR': 'pcr'}, inplace=True)

# Debugging: Check the data
print(df[['timestamp', 'pcr']].head())

# Create a figure
fig = make_subplots(rows=1, cols=1)

# Add a trace for the line plot
fig.add_trace(go.Scatter(x=df['timestamp'], y=df['pcr'], mode='lines', name='PCR over time'))

# Set up the layout
fig.update_layout(title='PCR over Time',
                  xaxis_title='Time',
                  yaxis_title='PCR Value',
                  xaxis=dict(tickformat='%H:%M'))

# Update frames for animation
frames = [go.Frame(data=[go.Scatter(x=df['timestamp'][:k+1], y=df['pcr'][:k+1])], name=f'frame{k}') for k in range(len(df))]

fig.update(frames=frames)

# Set up animation settings
fig.update_layout(updatemenus=[dict(type='buttons', showactive=False,
                                    buttons=[dict(label='Play', method='animate',
                                                  args=[None, dict(frame=dict(duration=100, redraw=True), fromcurrent=True)])])])

# Show the plot
fig.show()


ValueError: Excel file format cannot be determined, you must specify an engine manually.

In [10]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load the Excel file
excel_file_path = "/Users/tjzoomac/tj_nse/ai_market/01_nifty_live/002/Nifty_PCR.xlsx"
df = pd.read_excel(excel_file_path, sheet_name='TimeSeries', engine='openpyxl')

# Convert the 'Time' column to datetime, ensure it's correctly parsed
df['Time'] = pd.to_datetime(df['Time'], format='%H:%M')

# Rename columns for clarity
df.rename(columns={'Time': 'timestamp'}, inplace=True)

# Debugging: Check the data
print(df[['timestamp', 'Call', 'Put']].head())

# Create a figure
fig = make_subplots(rows=1, cols=1)

# Add traces for the line plots
fig.add_trace(go.Scatter(x=df['timestamp'], y=df['Call'], mode='lines', name='Call over time'))
fig.add_trace(go.Scatter(x=df['timestamp'], y=df['Put'], mode='lines', name='Put over time'))

# Set up the layout
fig.update_layout(title='Call and Put over Time',
                  xaxis_title='Time',
                  yaxis_title='Value',
                  xaxis=dict(tickformat='%H:%M'))

# Update frames for animation
frames = [go.Frame(data=[go.Scatter(x=df['timestamp'][:k+1], y=df['Call'][:k+1]),
                         go.Scatter(x=df['timestamp'][:k+1], y=df['Put'][:k+1])], name=f'frame{k}') for k in range(len(df))]

fig.update(frames=frames)

# Set up animation settings
fig.update_layout(updatemenus=[dict(type='buttons', showactive=False,
                                    buttons=[dict(label='Play', method='animate',
                                                  args=[None, dict(frame=dict(duration=100, redraw=True), fromcurrent=True)])])])

# Show the plot
fig.show()


            timestamp     Call      Put
0 1900-01-01 09:26:00  8422564  6438149
1 1900-01-01 09:27:00  8409317  6600867
2 1900-01-01 09:28:00  8409946  6600869
3 1900-01-01 09:29:00  8408303  6600777
4 1900-01-01 09:30:00  8408303  6600777
